In [1]:
import pandas as pd
from math import sqrt

In [24]:
def get_input_amount(spot_price, input_reserve, output_reserve):
    a = 997
    b = 1000
    I = input_reserve
    O = output_reserve
    P = spot_price
    
    input_amount = (
        sqrt(
            ((I*b - I*a)**2) + (4*P*O*I*a*b)
        ) - (I*b + I*a)
    )  / (2*a)

    return int(input_amount)

In [9]:
uniswap_history = pd.read_pickle('./uniswap_events.pickle')

In [10]:
uniswap_history.columns

Index(['transactionHash', 'transaction_index', 'transaction_sender', 'address',
       'data', 'topics', 'block_timestamp', 'blockNumber_dec', 'contract',
       'event', 'contract_event', 'block_group', 'agent', 'eth_delta',
       'token_delta', 'uni_delta', 'eth_balance', 'token_balance',
       'UNI_supply', 'invariant'],
      dtype='object')

In [11]:
uniswap_history.drop(columns=['transactionHash', 'transaction_index', 'transaction_sender', 'address',
       'data', 'topics', 'block_timestamp', 'blockNumber_dec', 'contract', 'agent', 'block_group', 'contract_event'], inplace=True)

In [7]:
uniswap_history

event             eth_delta            token_delta uni_delta  \
2         EthPurchase    -25326059253325791    5000000000000000000         0   
3         EthPurchase    -10118429075406013    2000000000000000000         0   
4       TokenPurchase     10000000000000000   -1964761376358359468         0   
5       TokenPurchase     10000000000000000   -1963452825230191574         0   
6       TokenPurchase     10000000000000000   -1962145581583193733         0   
...               ...                   ...                    ...       ...   
147434  TokenPurchase    555227276348537093  -71129353666089377834         0   
147435  TokenPurchase    494601926415615730  -63347970222414138488         0   
147436    EthPurchase  -2425103627055529511  312610256829251059712         0   
147437    EthPurchase  -1128145917100381911  145539841500000000000         0   
147438    EthPurchase   -963765746691049903  124391425500000000000         0   

                   eth_balance             token_balance  \
2         29974673940746674209    5905000000000000000000   
3         29964555511671268196    5907000000000000000000   
4         29974555511671268196    5905035238623641640532   
5         29984555511671268196    5903071785798411448958   
6         29994555511671268196    5901109640216828255225   
...                        ...                       ...   
147434  5013841555546109396965  661804343765215722063362   
147435  5014336157472525012695  661740995794993307924874   
147436  5011911053845469483184  662053606051822558984586   
147437  5010782907928369101273  662199145893322558984586   
147438  5009819142181678051370  662323537318822558984586   

                    UNI_supply                                       invariant  
2         30000000000000000000      177000449620109111204145000000000000000000  
3         30000000000000000000      177000629407442181233772000000000000000000  
4         30000000000000000000      177000806558499339943044863018842396120272  
5         30000000000000000000      177000983650652913895410492180545782739768  
6         30000000000000000000      177001160683942120400286097646701713324100  
...                        ...                                             ...  
147434  3304234867026987131356  3318182120410961321903054254127069667340496330  
147435  3304234867026987131356  3318191802096709075939561492313859130956275430  
147436  3304234867026987131356  3318153786409383294318328983695028281242201824  
147437  3304234867026987131356  3318136161887025149934194878087918636279977978  
147438  3304234867026987131356  3318121135577318262538972182684328470346182820  

[135609 rows x 8 columns]

In [63]:
def calc_input_amount(row):
    if(row.event == 'TokenPurchase'):
        balances = uniswap_history.iloc[row.name-1] 
        input_reserve, output_reserve = balances.eth_balance, balances.token_balance 
        spot_price = row.eth_balance // row.token_balance
        return get_input_amount(spot_price, input_reserve, output_reserve)
    elif(row.event == 'EthPurchase'):
        balances = uniswap_history.iloc[row.name-1] 
        input_reserve, output_reserve = balances.token_balance, balances.eth_balance 
        spot_price = row.token_balance // row.eth_balance
        return get_input_amount(spot_price, input_reserve, output_reserve)

def calc_spot_price(row):
    if(row.event == 'TokenPurchase'):
        spot_price = row.eth_balance / row.token_balance
        return spot_price
    elif(row.event == 'EthPurchase'):
        spot_price = row.token_balance / row.eth_balance
        return spot_price
    
def calc_error(row):
    if(row.event == 'TokenPurchase'):
        return ((row.calculated_input) - abs(row.eth_delta)) // (10**18)
    elif(row.event == 'EthPurchase'):
        return ((row.calculated_input) - abs(row.token_delta)) // (10**18)

input_compare = []
input_compare = uniswap_history[['event', 'eth_balance', 'eth_delta', 'token_balance', 'token_delta']]
input_compare['calculated_input'] = uniswap_history.apply(lambda x: calc_input_amount(x), axis=1)
input_compare['spot_price'] = uniswap_history.apply(lambda x: calc_spot_price(x), axis=1)
input_compare['error'] = input_compare.apply(lambda x: calc_error(x), axis=1)
input_compare

<ipython-input-63-07feb25c7269>:29: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy

<ipython-input-63-07feb25c7269>:30: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy



event             eth_balance             eth_delta  \
0        AddLiquidity    30000000000000000000  30000000000000000000   
1            Transfer    30000000000000000000                     0   
2         EthPurchase    29974673940746674209    -25326059253325791   
3         EthPurchase    29964555511671268196    -10118429075406013   
4       TokenPurchase    29974555511671268196     10000000000000000   
...               ...                     ...                   ...   
147434  TokenPurchase  5013841555546109396965    555227276348537093   
147435  TokenPurchase  5014336157472525012695    494601926415615730   
147436    EthPurchase  5011911053845469483184  -2425103627055529511   
147437    EthPurchase  5010782907928369101273  -1128145917100381911   
147438    EthPurchase  5009819142181678051370   -963765746691049903   

                   token_balance             token_delta  calculated_input  \
0         5900000000000000000000  5900000000000000000000               NaN   
1         5900000000000000000000                       0               NaN   
2         5905000000000000000000     5000000000000000000     -1.002352e+19   
3         5907000000000000000000     2000000000000000000      5.391248e+15   
4         5905035238623641640532    -1964761376358359468     -2.996456e+19   
...                          ...                     ...               ...   
147434  661804343765215722063362   -71129353666089377834     -5.013286e+21   
147435  661740995794993307924874   -63347970222414138488     -5.013842e+21   
147436  662053606051822558984586   312610256829251059712      7.579786e+19   
147437  662199145893322558984586   145539841500000000000     -2.410789e+20   
147438  662323537318822558984586   124391425500000000000     -3.885976e+20   

        spot_price   error  
0              NaN     NaN  
1              NaN     NaN  
2       196.999641   -16.0  
3       197.132909    -2.0  
4         0.005076   -30.0  
...            ...     ...  
147434    0.007576 -5014.0  
147435    0.007577 -5015.0  
147436  132.096041  -237.0  
147437  132.154827  -387.0  
147438  132.205079  -513.0  

[147439 rows x 8 columns]

In [66]:
import plotly.express as px
df = input_compare.drop(input_compare.loc[(input_compare['event'] != 'EthPurchase') & (input_compare['event'] != 'TokenPurchase')].index)
# df = df.loc[(df['error'])]
fig = px.line(x=df.index, y=df.error, facet_row=df.event)
fig.show()

In [26]:
I = 5900000000000000000000
O = 30000000000000000000
a = 997
b = 1000
Delta_I = 5000000000000000000 

spot_price_a = ((Delta_I*2*a + (I*b + I*a))**2 + (I*b - I*a)**2) // (4*O*I*a*b)

In [27]:
spot_price_b = 5905000000000000000000//29974673940746674209

In [28]:
spot_price_c = 5000000000000000000//25326059253325791

In [29]:
print(spot_price_a)
print(spot_price_b)
print(spot_price_c)

197
196
197


In [30]:
print(get_input_amount(spot_price_a, I, O))
print(5000000000000000000)

5005391241128905728
5000000000000000000


In [31]:
print(get_input_amount(spot_price_b, I, O))
print(5000000000000000000)

-10023524237629900800
5000000000000000000


In [32]:
print(get_input_amount(spot_price_c, I, O))
print(5000000000000000000)

5005391241128905728
5000000000000000000
